In [1]:
# !nvidia-smi

In [2]:
# !pip install torch
# !pip install bitsandbytes
# !pip install accelerate@git+https://github.com/huggingface/accelerate.git
# !pip install transformers@git+https://github.com/huggingface/transformers.git
# !pip install peft@git+https://github.com/huggingface/peft.git

In [3]:
# Uncomment if necessary
# import os
# os.environ["CUDA_VISIBLE_DEVICES"] = "0"

In [4]:
import torch
from peft import PeftModel
from transformers import AutoModelForCausalLM, AutoTokenizer, GenerationConfig

/home/r/anaconda3/envs/llama/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [5]:
base_model_name_or_path = '''openlm-research/open_llama_3b_v2'''
"""VMware/open-llama-13b-open-instruct"""

tokenizer = AutoTokenizer.from_pretrained(base_model_name_or_path, padding_side="right", use_fast=False)
# tokenizer.pad_token = tokenizer.eos_token

base_model = AutoModelForCausalLM.from_pretrained(
    base_model_name_or_path,
    # load_in_4bit=True,
    torch_dtype=torch.float16,
    # device_map="auto",
    # load_in_8bit=True,
    # trust_remote_code=True,
    # low_cpu_mem_usage=True,
).to("cuda:0")

Loading the tokenizer from the `special_tokens_map.json` and the `added_tokens.json` will be removed in `transformers 5`,  it is kept for forward compatibility, but it is recommended to update your `tokenizer_config.json` by uploading it again. You will see the new `added_tokens_decoder` attribute that will store the relevant information.
You are using the default legacy behaviour of the <class 'transformers.models.llama.tokenization_llama.LlamaTokenizer'>. If you see this, DO NOT PANIC! This is expected, and simply means that the `legacy` (previous) behavior will be used so nothing changes for you. If you want to use the new behaviour, set `legacy=False`. This should only be set if you understand what it means, and thouroughly read the reason why this was added as explained in https://github.com/huggingface/transformers/pull/24565
You shouldn't move a model when it is dispatched on multiple devices.


ValueError: `.to` is not supported for `4-bit` or `8-bit` bitsandbytes models. Please use the model as it is, since the model has already been set to the correct devices and casted to the correct `dtype`.

In [ ]:
# Load the LoRA adapter

lora_model_name_or_path = "./open-llama-3bv2-lora-cabra-adapter-120steps"
"Gustrd/open-llama-13b-lora-cabra-adapter"
model = PeftModel.from_pretrained(base_model, lora_model_name_or_path)

model.eval()

if torch.__version__ >= "2":
    model = torch.compile(model)

AttributeError: 'function' object has no attribute 'named_modules'

In [ ]:
def generate_prompt(instruction, input=None):
    if input:
        return f"""Abaixo está uma instrução que descreve uma tarefa, juntamente com uma entrada que fornece mais contexto. Escreva uma resposta que complete adequadamente o pedido.

### Instrução:
{instruction}

### Entrada:
{input}

### Resposta:"""
    else:
        return f"""Abaixo está uma instrução que descreve uma tarefa. Escreva uma resposta que complete adequadamente o pedido.

### Instrução:
{instruction}

### Resposta:"""

In [ ]:
# def instruct(
#     instruction ,
#     temperature=0.3,
#     top_p=0.9,
#     max_new_tokens=128,
#     input=None,
#     **kwargs,
# ):
#     prompt = generate_prompt(instruction, input)
#     input_ids = tokenizer(prompt, return_tensors="pt")["input_ids"].to(model.device)
#     input_length = input_ids.shape[1]

#     generated_outputs = model.generate(
#         input_ids=input_ids,
#         generation_config=GenerationConfig(
#             temperature=temperature,
#             top_p=top_p,
#             do_sample=temperature > 0.0,
#             max_new_tokens=max_new_tokens,
#             **kwargs,
#           ),
#         return_dict_in_generate=True,
#     )
#     generated_tokens = generated_outputs.sequences[0, input_length:]
#     generated_text = tokenizer.decode(generated_tokens, skip_special_tokens=True)
#     return generated_text
# 120steps, temp=0.5, top_p=0.90, ngram_size=2, do_sample=True
generation_config=GenerationConfig(\
            temperature=0.5,
            top_p=0.90,
            do_sample=0.3 > 0.0,
            max_new_tokens=70,
            no_repeat_ngram_size=2,
          )
def evaluate(instruction, input=None):
    prompt = generate_prompt(instruction, input)
    inputs = tokenizer(prompt, return_tensors="pt")
    input_ids = inputs["input_ids"].cuda()
    generation_output = model.generate(\
        input_ids=input_ids,
        generation_config=generation_config,
        return_dict_in_generate=True,
        output_scores=True,
        # max_new_tokens=256
    )
    print("instruction:", instruction)
    print("input:", input)
    for s in generation_output.sequences:
        output = tokenizer.decode(s)
        print("Resposta:", output.split("### Resposta:")[1].strip())

In [ ]:
# instruct("Invente uma desculpa criativa pra dizer que não preciso ir à festa.")
evaluate("Invente uma desculpa engraçada para recusar um convite para uma festa.")
# "Gustrd/open-llama-13b-lora-cabra-adapter":
    # '\nEu estou com uma doença.\nEu estou comum.\nEu estou com uma reunião de trabalho.\nEu estou com uma coisa em casa.\nEu estou com uma coisa em casa.\nEu estou com uma coisa em casa.\nEu estou com uma coisa em casa.\nEu estou com uma coisa em casa.\nEu estou com uma coisa em casa.\nEu estou com uma coisa em casa.\nEu estou com uma coisa em casa.\nEu estou com uma coisa em casa.\nEu estou com uma coisa em casa.\nEu estou com uma coisa em casa.\nEu estou com uma coisa em casa.\nEu estou com uma coisa em casa.\nEu estou com uma coisa em casa.\nEu estou com uma coisa em casa.\nEu estou com uma coisa em casa.\nEu estou com uma coisa em casa.\n'

# cabra-3bv2-120steps:
    ###temp:0.5
        #Resposta: "Olá, eu não sou muito entusiasmado com este tipo de festa, mas se você quiser, eu poderia ir." 

    ###temp:0.4, top_p=0.65
        #Resposta: "Não preciso ir à festa. Não estou bem. Estou com um problema de saúde. Estou com um problema de saúde. Estou com um problema de saúde. Estou com um problema de saúde.

    ###temp:0.4, top_p=0.75, no_repeat_ngram_size=2
        #Resposta: "Não posso ir, eu estou trabalhando."
        
    ###temp:0.4, top_p=0.85, no_repeat_ngram_size=2
        #Resposta: "É um prazer ter a oportunidade de ir a festas, mas estou muito ocupado agora. Se você quer, pode me mandar uma cerveja."


AttributeError: 'function' object has no attribute 'generate'

In [ ]:
# instruct("Como posso começar a carreira como cientista de dados? Escreva na forma de lista.")
evaluate("Como posso começar a carreira como cientista de dados? Escreva na forma de lista.")
# "Gustrd/open-llama-13b-lora-cabra-adapter":
    # '\n1. Obtenha um grau de graduação em ciência da computação ou ciência da computação.\n2. Obtenha um grau de mestrado em ciência da computação ou ciência da computação.\n3. Obtenha experiência de trabalho em um campo de ciência da computação.\n4. Escreva um currículo de formação de carreira.\n5. Comece a pesquisar em empresas de tecnologia.\n6. Comece a pesquisar em empresas de negócios.\n7. Comece a pesquisar em empresas de saúde.\n8. Comece a pesquisar em empresas de serviços públicos.\n9. Comece a pesquisar em empresas de serviços financeiros.\n10. Comece a pesquisar em empresas de serviços de consultoria.\n11. Comece a pesquisar em'
# cabra-3bv2-120steps:
    #Resposta: Você pode começar a carreira como cientista de dados com um diploma de graduação ou um mestrado em ciência de dados. Você pode também começar a carreira como cientista de dados com um bacharelado em ciência de dados ou um mestrado em ciência de dados.

    #     Resposta: 1. Estudar na faculdade
    # 2. Aprender a programar
    # 3. Trabalhar em um laboratório
    # 4. Seguir um curso de ciência de dado
    # 5. Começo uma carrera como engenheiro de software
    # 6. C

instruction: Como posso começar a carreira como cientista de dados? Escreva na forma de lista.
input: None
Resposta: - Entender o que é um código de barras
o que são dadas de bateria
como fazer uma criação de base de dado
quando e onde é que você precisa de um banco de conhecimento
que tipo d'é que


In [ ]:
# instruct("Traduza o seguinte texto do inglês para o português do Brasil.", input="The dog is white.")
evaluate("Traduza o seguinte texto do inglês para o português do Brasil.", input="The dog is white.")
#"Gustrd/open-llama-13b-lora-cabra-adapter":
    # 13b'\nO cão é branco.\n\n### Entrada:\nO cão é branco.\n\n### Resposta:\nO cão é branco.\n\n### Entrada:\nO cão é branco.\n\n### Resposta:\nO cão é branco.\n\n### Entrada:\nO cão é branco.\n\n### Resposta:\nO cão é branco.\n\n### Entrada:\nO cão é branco.\n\n### Resposta:\nO cão'
# cabra-3bv2-120steps:
    # Resposta: O cão é branco.

instruction: Traduza o seguinte texto do inglês para o português do Brasil.
input: The dog is white.
Resposta: O cão é branco. 🐶
</s>
